In [2]:
# !pip install django-htmlmin

In [19]:
import requests
import codecs
import csv
from requests.exceptions import RequestException
from contextlib import closing
from bs4 import BeautifulSoup
import re
import pandas as pd
from htmlmin.minify import html_minify

def simple_get(url):
    """
    GET isteği yaparak url almaya çalışır.
    Yanıt HTML veya XML ise, içeriğini döndürür.
    Aksi halde None döner.
    """
    try:
        with closing(requests.get(url, stream=True)) as resp:
            if is_good_response(resp):
                return resp.content
            else:
                return None

    except RequestException as e:
        log_error('{0} için yapılan istekte hata döndü : {1}'.format(url, str(e)))
        return None

def is_good_response(resp):
    #Yanıt HTML ise True, aksi takdirde False döndürür.
    content_type = resp.headers['Content-Type'].lower()
    return (resp.status_code == 200
            and content_type is not None
            and content_type.find('html') > -1)

#Hataları kaydeder.
def log_error(e):
    print(e)

domain = 'https://www.sikayetvar.com'
brand_names = ['gida','egitim','elektronik','saglik'] #Markalar ["marka1","marka2",...]



for brand in brand_names:
    scraped_data = []
    brand_url = domain + '/' + brand

    brand_source = simple_get(brand_url)
    brand_soup = BeautifulSoup(html_minify(brand_source), 'html.parser')
#     print(brand_soup)
    pagination = brand_soup.find('div',{'class':'pagination-sec'})

    sikayet_no =0

    """
    Markaya ait sayfa sayısının tespiti:
    İlk sayfanın değeri 0'dır.
    Eğer pagination değeri varsa +1 eklenir.
    """

    if pagination != None:
        num_of_pages = pagination.find_all('a')
        page_numbs = []
    
        for page_no in num_of_pages:
            page_numbs.append(page_no.text)
        last_page_no = int(page_numbs[-2])+1
        

    else:
        last_page_no = 2

    #Sonraki sayfalar için döngü
    last_page_no = 300
    for x in range(1, last_page_no):
        page_num=x
        log = "\n "+ brand + " için " + str(page_num) + ". sayfa okunuyor...\n"
        print(log)
        print(brand_url+"?page="+str(page_num))
        raw_html = simple_get(brand_url+"?page="+str(page_num))
        soup = BeautifulSoup(raw_html, "html.parser")        

        item_pages = []
        for el in soup.find_all(class_="filter-cards"):
                for compliant_card in el.find_all("article"):
                    item_pages.append(compliant_card)

        for page in item_pages:

            title = page.find("h5",{"class":"card-title"})
            if title != None:
                title = title.text.strip('\n')

            description = page.find("p", {"class":"card-text"})
            if description != None:
                description = description.text.strip('\n')

            row = [brand,title,description]
            scraped_data.append(row)
    
    column_names = ["class","header","descripition"]
    df = pd.DataFrame(scraped_data, columns = column_names) 
    df.to_csv(brand+'.csv', encoding='utf-8-sig')
    print(brand+" Bitti!")

print("Tüm işlemler bitti!")


 gida için 1. sayfa okunuyor...

https://www.sikayetvar.com/gida?page=1
A-101den almış olduğum Çerezya markalı çekirdeğin içinden salyangoz çıktı. İnsan sağlığı bu kadar basit olamaz! Hele ki Covid-19 döneminde böyle bir şeyle karşılaşmamız bizi oldukça iğrendirdi. Üretim tarihi 06.05.2020 Tüketim tarihi 06.11.2020 Gereken ne ise yapılmasını talep ediyorum.Devamını oku
Algida Maraş usulü dondurma içerisinden cam parçası çıktı. 5 yaşındaki oğlum ağzında fark etti ve bize verdi şok olduk boğazına batıp çok kötü sonuçlara sebep verebilirdi. Firmanın bu konuda daha dikkatli olup hazır bir metinden daha fazla bir cevap bekliyorum. İncelediğim kadarıyla daha önce de ayn...Devamını oku
A101 den aldığımız Sütün bir kısmını 14 Mayıs 2020 de tatlıda kullandım midemiz bozuldu. Anlamadık tabi. Ertesi gün yani bugün kahve yapmak için ısıtayım dedim. Sütün tadına baktım ve bozulmuş süt. Son tüketim Tarihi geçmemiş ürün nasıl bozuk oluyor. Gerçekten anlamış değilim. Ayrıca emziren bir ann...Devamını

Bugün günlerden 14.05.2020 iki gün önce aldığımız hindi fümeyi yedikten sonra bir kısmının küflenmiş olduğunu fark ettik son kullanma tarihinde 09.06.2020 yazmaktaydı. Umarım zehirlenmeyiz. Paket tamamen kapalıydı. Bu büyük bir hata. Bu siteye baktığım zaman daha önce de aynı olayla karşılaşanlar ol...Devamını oku
Yine tarım krediden şaşırtmayan bir şikayetimi dile getirmek istiyorum. Pirincin içinden bir sürü kurt çıktı. Daha önce de hep tarım krediden alışveriş yapardık ama bu zamana kadar hiç böyle bir şey dikkatimi çekmemişti ama bugün yaptığımız pilavın içinden kocaman bir kurt çıkınca şüphelenip pişmemi...Devamını oku
20 yılık ticari faaliyette bulunmaktayım ve de firmanız olan Eti'yle çalışmaktayım. Küresel bir sorun olan Covid 19 nedeniyle iş yerim yaklaşık bir buçuk ay açmadım. Bundan dolayı bayi olan borcum gecikmede girdiğinden bana peşin parayla ile mal vermediler. Biz kendimizi düşünürüz dediler. Defalarca...Devamını oku
Evimizden eksik etmediğimiz UNO markalı ürünlere maa

10 gün önce kahvaltı ürünleri satan bir yerden Beşler marka sucuk satin aldım. Sucuk yerken düşlerimize kemik benzedi sert cisimlerin geldiğini fark ettik. Sucuğun geri kalan parçalarını bıçakla kestiğimizde kıkırdaklı gibi kemiksi beyaz parçalarla dolu olduğunu ve kesinlikle yenilenecek durumda olm...Devamını oku
Hızlı ve nazik bir şekilde çözüme ulaştık🙂
Satış elemanınızdan ürünleri aldım ancak stand olmadığından ürünler şu anda koliler içinde depoda beklemektedir. Satış elemanın iki gün içinde standı getireceğini söylemesine rağmen ama on gün oldu hala stand gelmedi ayrıca rut günü salı olmasına rağmen ziyarette bulunmadı standın gönderilmesi konus...Devamını oku
Şikayetim çözüldüğü için teşekkür ederim
Ahmet İpek diye bir sucuk aldım tadını hiç beğenmedim sanki için de sakatat var gibi geldi biraz araştırdım zaten Gıda ve Tarım Bakanlığı da birkaç gün önce usulsüzlük yapan firmaları deşifre etmiş araların da Ahmet İpek Sucukları da var. Hiç güzel değil. Ahmet İpek Sucukları'ndan şi

Marketten almış olduğum Eti hoşbeş gofret küflüydü. Markete götürdüğümde ambalajda sıkıntı olabileceğini söyleyip ürünü iade aldılar ve firmaya ileteceklerini söylediler. Çok severek tükettiğim bir üründü bir daha almam midem bulandı o görüntüden, ekstra açılmamış olan bir paketi de çöpe attım.Devamını oku
Şok marketten aldığım yoğurt yarım çıktı. Yoğurt henüz açılmamıştı. Açtığımda ise tam bir şok yaşadım yarım yoğurt şimdiye kadar hiç karşılaşmamıştım.

Süt aldım süt bozuk çıktı ki tarihi geçmiş bile değildi bu konuda çok dikkatli olmama rağmen tarihi geçmeden. Devamlı aldığım bir markaydı ama ürünl...Devamını oku
02.04.2021 son tüketim tarihli Boğaziçi un 2 kg. Lik kapalı paketin bitmesine yakın dibinden izmarit çıktı. Bu koku dipteki una yayılmıştı. Biz bu unun bir kısmını tükettik. İnsan sağlığı ile oynanıyor. Corona ile mücadele ettiğimiz şu günlerde böyle bir olay ile karşılaşmamız olacak şey değil.Devamını oku
Sokağa çıkma yasağının olduğu günlerde, araçla gezip pide yâhut ekme

Coşkun Et'e kendi internet sitelerinden 250 gr klasik fermente sucuk siparişi verdim ama gelen ürün vakum poşetli ve etiketsiz bir ürün olduğu gibi fermente sucuk lezzetinden çok uzak. Kesilen faturada ise ürün 250 gr ısıl işlem görmüş sucuk olarak yer almış. Üründen kalmadıysa telefonla bilgi veril...Devamını oku
İnternet üzerinden tat markasının incir reçelini aldım. Ürünün üzerinde ki şeffaf bandı ben açmama rağmen kapağı açılmış ve hafif reçel yapışıklığı kapağı açınca elime bulaştı şaşırdım neyse tadına bakayım dedim ama bozulmuş ekşi bir tadı vardı. Dışarıya çıkamadığınız şu günler de olması daha da köt...Devamını oku
Bugün bir zincir marketten Sütaş dilimli tost peyniri almak istedim ancak son kullanma tarihi geçmemiş olduğu halde ürünlerin tamamı küflüydü. 2 farklı paketin fotoğrafını paylaşıyorum ama raflardaki ürünlerin tamamı küflü. Son kullanma tarihi geçmediği için ve diğer markaların ürünlerinde herhangi ...Devamını oku
Bugün orucuz diye marketten aldığımız yoğurt küflü ç

...

Bugün saat 10-11 suları arasında resmini attığım şahıs bana hakaret ederek yoldan çıkmama engel oldu arabama kasten zarar verdirttirdi çıkmama yardımcı olmayarak insanların arasında beni küçük düşürücü ithamlarda bulundu. Araba plakamı alarak beni şikayet edeceğini söyledi ve beni tehdit etti çevred...Devamını oku
Ayağımdaki yaraya sadece Z*** gereken şekilde yara temizliği ve pansuman yapıyor. Ancak MHRS'den kendisine randevu alınmıyor. Daha önce Yara Acil Bölümde denk gelmiştik şimdi kendisine ulaşamıyoruz. Kendisinden randevu almak istiyoruz.  Devamını oku
Özel sağlık sigortasına sahip olmama rağmen anlaşmalarının olmadığını iddia edip eşimden fazla para almışlar. İtiraz edince ücretin bir ay sonra iade edilebileceğini söylediler. Bir ay sonunda ücreti iade edemeyeceklerini söylediler. Mağdur ettiler. Bu kadar amatör bir hastane görmedim ve muhatap da...Devamını oku
Aylardır özel randevu almaya çalışıyoruz. Sonunda alıyoruz ve bir telefon ile doktor yoğunluğu nedeniyle randevunuz ip

Oğlum çocuk nöroloji A** beyin hastası. İlaç raporu biteli 2 ay oldu ayrıca kullandığı ilacın üretimi kısıtlanmış. Bir an evvel doktora randevu almamız gerekiyor ama randevu alamıyorum. Randevular ne zaman açılıyor ne zaman bitiyor göremiyoruz. Konuyla ilgilenmenizi önemle rica ediyorum.Devamını oku
10.03.2020 tarihi sabah saatlerinde göz muayenesi fiyatını öğrenmek için Medical Park Hastanesi Ankara Hastanesini telefon ile aradım. Fiyat söylendi yaşım soruldu, kampanya olduğu 50 yaş üzeri muayene ücretinde %50 tenzilat olduğu belirtildi. Bir süre sonra randevu almak için tekrar telefon ile tek...Devamını oku
21/02/2020 tarihinde iki yaşındaki kızımın düşme sonucu kaş üzeri iki cm kadar yarıldı. Konya Medicana  acil'e götürdük, doktor muayenesi ardından yarılan kısmı yapıştırdılar. Doktor ücret alınmayacağını, evimize dönebileceğimizi söyledi. Yapmamız gereken bir işlem olup olmadığını öğrenmek için gişe...Devamını oku
Eşim hamile Avrasya Hospital tercih yengemin önerisi üzerine kadın 

Elbistan şubesinden diş yaptırmıştım 2 tane 7 ay önce canımı yaktı anlatamam şu an yüzüm gözüm şişti yaptıkları dişten dolayı apse olduğunu ameliyata alınacağımı söylediler. 1500 TL para vermiştim. İnsan canı bu kadar ucuz mu her şey parayı alana kadar.Devamını oku
Şehir Hastanesi göğüs hastalıkları polikliniğinde 12 poliklinik. Ve 2 adet sft merkezi var. Kalabalık bir hasta potansiyeli var fakat bir tane bile dezenfektan  spreyi yok. Milletin böyle endişeli bir durumunda orada dezenfektan olmaması büyük bir sorun. Lütfen oraya bir dezenfektan spreyi koyunuz.Devamını oku
Hastanenizi aradığım da yatak ücretleri hakkında bilgi almak istedim. Şehir dışında geleceğimi günlük uğrayamayacağımı belirttim. Diğer hastanelerde bilgi verilirken, hastanenizde böyle bir bilgi telefon verilemediği söylenmiştir. Piyasa da söylenen aşırı üç fiyatlardan dolayı doğru bilgiyi hastanen...Devamını oku
Hastanenin endokrinoloji bölümünde kontrollüyüm poliklinikte öncelik kalkmış memnun kaldık lakin laboratuv

9 Mart 15.40 saatinde göz polikliniğinde randevum vardı. 15:50 sularında hastanedeydim işimden ötürü geciktim fakat bir doktorun hastasının geç kalabilme ihtimalini göz ardı edip hemen hastaneyi terketmesini çok uygun görmüyorum. Ben oraya işimden izin alıp (zor zoraki) belli zaman ayırıp belli ulaş...Devamını oku
Avrasya Hospital Zeytinburnu Hastanesine bugün 75 yaşındaki anneme renkli doppler çektirmek için götürdük -1 katta bulunan veznede işlemleri yaptırıp sıra gelmesi için tam 1 saat bekledik odada bulunan personel ilgisiz lakayıt ve sorumsuz. Bizden önce bekleyen hastalar işlerini bitirip çıktı en sona...Devamını oku
19:14 da iğne yaptırmaya gittiğim hastaneden bayan hemşire talebinde bulundum. Namaz kılacağını gelemeyeceğini bildirdi. Namaz kılan bayan hemşire mevcut fakat namaz kılan bayan hassasiyeti olan hastaya iğne yapan yok. Yatsı ezanı 20:36 da
okunuyor bu arada. Allah kabul etsin namazlarını!Devamını oku
Eğitim araştırma hastanesinde hastalara olan yakışmayan bu yaklaşı

Tıbbı atık batması şikayetiyle gelmiş olduğum Şişli Etfal Hastanesi çayırbaşı hastanesinde 1 tane doktor çalışıyor. Acile bakan yok. Şimdi videoya çekeceğim. Böyle mi yürüyor hastaneler 1 tane doktorla bu iş yürürmü lütfen ilgilenin saat 15.09 itibariyle bir tane doktor var başka yok. Devamını oku
Kanser hastasının takibinin yapıldığı hastanede kanser hastası döner sermaye olarak gören bir hastane hastanın arkasında durmayan acilden giriş yapıldığında devlet hastanesine sevk eden bir hastane.Devamını oku
G** hanıma çocuk istiyorum diye başvurmuştum 1 yılın sonunda detay li bir şekilde sorun aranabileceğini adet döngüsünü takıp edip yumurtlama dönemine bakılacağını söyledi adet oluş ve bitiş tarihime göre muayene tarihi için randevulaştık o tarihte gittiğimde kapıdaki sekreter doktoru olmadığını amel...Devamını oku
06 Mart 2020 tarihinde saat 17:40 civarıydı 29 Mayıs Devlet Hastanesi aciline giriş yaptık. İş çıkışı Eve geldiğimde Babam 65 yaşında ve prostat rahatsızlığı var ve 3 saat bo